In [1]:
from analytics_cloud_core import Clients, ClientType
import pandas as pd
import numpy as np
from datetime import date
from pygsuite import Spreadsheet
from google.cloud import bigquery

In [2]:
def read_google_spreadsheet(sheet_id, sheet_name):

    # authenticate to the pygsuite package
    Clients.get_client(ClientType.PYGSUITE)
    sheet = Spreadsheet(id = sheet_id)
    df = sheet.worksheets[sheet_name].dataframe

    return df

sheet_id = '1GxuvblcWKHmYaAVHLfk0QGLHm0eHDIkA1CGbI_4EsA4'
web_sheet_name = 1
app_sheet_name = 2

web = read_google_spreadsheet(sheet_id, web_sheet_name)
app = read_google_spreadsheet(sheet_id, app_sheet_name)

web = web[web['Page']!=""]
app = app[app['Page']!=""]
gsheet = pd.concat([web,app])

In [3]:
client = bigquery.Client(project = 'wf-gcp-us-ae-sf-prod')

query = f"""
select * from `wf-gcp-us-ae-sf-prod.foundation_quality.tbl_page_type_budget`
"""
query_job = client.query(query)  # Make an API request.
past_slo = query_job.to_dataframe()

In [4]:
client = bigquery.Client(project = 'wf-gcp-us-ae-sf-prod')

query = f"""
select distinct pt.PageGroupName, 
  slo.PageID
from `wf-gcp-us-ae-sf-prod.foundation_quality.tbl_page_type_budget` slo
left join `wf-gcp-us-ae-sf-prod.performance.tbl_page_type_grouping` pt
on slo.pageid = pt.pageid
where startdate = '2022-01-01T00:00:00' and pagegroupname is not null
"""
query_job = client.query(query)  # Make an API request.
pageid = query_job.to_dataframe()

In [5]:
new_slo = gsheet.merge(pageid, how = 'left', left_on = 'Page', right_on = 'PageGroupName')[['PageGroupName','PageID','PlatformID','Percentile','SLO (New)']]
new_slo['Percentile'] = new_slo['Percentile'].str[-2:]
new_slo['SLO (New)'] = new_slo['SLO (New)'].astype(int)
new_slo['SpeedIndexBudget75th'] = new_slo[['PageID','PlatformID','Percentile','SLO (New)']].apply(
    lambda x: x['SLO (New)'] if x['Percentile'] == '75' else None, axis = 1)
new_slo['SpeedIndexBudget95th'] = new_slo[['PageID','PlatformID','Percentile','SLO (New)']].apply(
    lambda x: x['SLO (New)'] if x['Percentile'] == '95' else None, axis = 1)
new_slo = new_slo.drop(columns = ('Percentile'))
new_slo = new_slo.groupby(['PageGroupName','PageID','PlatformID']).agg(
    {'SpeedIndexBudget75th':'max','SpeedIndexBudget95th':'max'})
new_slo = new_slo.reset_index()

In [6]:
new_slo['StartDate'] = date.today()
new_slo['SpeedIndexBudget'] = np.nan
new_slo['SpeedIndexGoal'] = np.nan
new_slo['TotalPageLoadTimeBudget'] = np.nan
new_slo['TotalPageLoadTimeGoal'] = np.nan
new_slo['HTMLSizeBudget'] = np.nan
new_slo['HTMLSizeGoal'] = np.nan
new_slo['SpeedIndexBudget99th'] = np.nan 
new_slo['SpeedIndexGoal99th'] = np.nan
new_slo['TotalPageLoadTimeBudget99th']=np.nan
new_slo['TotalPageLoadTimeGoal99th'] = np.nan
new_slo['SpeedIndexGoal75th']=np.nan
new_slo['SpeedIndexGoal95th']=np.nan
new_slo['ingest_timestamp']= np.nan
new_slo['event_date']=np.nan
new_slo = new_slo.drop(columns = 'PageGroupName')
#new_slo.dtypes

In [7]:
pd.set_option('display.max_rows', 5000)
update_slo_table = pd.concat([new_slo, past_slo])
update_slo_table = update_slo_table[['PageID', 'PlatformID', 'StartDate', 'SpeedIndexBudget',
       'SpeedIndexGoal', 'TotalPageLoadTimeBudget',
       'TotalPageLoadTimeGoal', 'HTMLSizeBudget', 'HTMLSizeGoal',
       'SpeedIndexBudget99th', 'SpeedIndexGoal99th',
       'TotalPageLoadTimeBudget99th', 'TotalPageLoadTimeGoal99th',
       'SpeedIndexBudget75th', 'SpeedIndexGoal75th',
       'SpeedIndexBudget95th', 'SpeedIndexGoal95th', 'ingest_timestamp',
       'event_date']]

update_slo_table['PlatformID']= update_slo_table['PlatformID'].astype(int)
update_slo_table['StartDate'] = pd.to_datetime(update_slo_table['StartDate'])
update_slo_table['ingest_timestamp'] = pd.to_datetime(update_slo_table['ingest_timestamp'])
update_slo_table['event_date'] = pd.to_datetime(update_slo_table['event_date'])
#update_slo_table.dtypes

/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/pandas/core/indexes/base.py:2023: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior.  In a future version these will be considered non-comparable.Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  return self._engine.is_unique
/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/pandas/core/indexes/base.py:3512: FutureWarning: Comparison of Timestamp with datetime.date is deprecated in order to match the standard library behavior.  In a future version these will be considered non-comparable.Use 'ts == pd.Timestamp(date)' or 'ts.date() == date' instead.
  indexer = self._engine.get_indexer(target._get_engine_target())


In [8]:
#new_slo
update_slo_table

PageID  PlatformID               StartDate  SpeedIndexBudget  \
0          125           1 2023-03-20 00:00:00.000               NaN   
1          125           2 2023-03-20 00:00:00.000               NaN   
2          125           3 2023-03-20 00:00:00.000               NaN   
3          125           4 2023-03-20 00:00:00.000               NaN   
4          114           1 2023-03-20 00:00:00.000               NaN   
5          114           2 2023-03-20 00:00:00.000               NaN   
6          114           3 2023-03-20 00:00:00.000               NaN   
7          114           4 2023-03-20 00:00:00.000               NaN   
8         1551           1 2023-03-20 00:00:00.000               NaN   
9         1551           2 2023-03-20 00:00:00.000               NaN   
10        1551           3 2023-03-20 00:00:00.000               NaN   
11        1551           4 2023-03-20 00:00:00.000               NaN   
12        2517           1 2023-03-20 00:00:00.000               NaN   
13        2517           2 2023-03-20 00:00:00.000               NaN   
14        2517           3 2023-03-20 00:00:00.000               NaN   
15        2517           4 2023-03-20 00:00:00.000               NaN   
16         293           1 2023-03-20 00:00:00.000               NaN   
17         293           2 2023-03-20 00:00:00.000               NaN   
18         336           1 2023-03-20 00:00:00.000               NaN   
19         336           2 2023-03-20 00:00:00.000               NaN   
20         336           3 2023-03-20 00:00:00.000               NaN   
21         336           4 2023-03-20 00:00:00.000               NaN   
22         665           1 2023-03-20 00:00:00.000               NaN   
23         665           2 2023-03-20 00:00:00.000               NaN   
24         665           3 2023-03-20 00:00:00.000               NaN   
25         665           4 2023-03-20 00:00:00.000               NaN   
26         373           1 2023-03-20 00:00:00.000               NaN   
27         373           2 2023-03-20 00:00:00.000               NaN   
28         373           3 2023-03-20 00:00:00.000               NaN   
29         373           4 2023-03-20 00:00:00.000               NaN   
30        2708           1 2023-03-20 00:00:00.000               NaN   
31        2708           2 2023-03-20 00:00:00.000               NaN   
32        2708           3 2023-03-20 00:00:00.000               NaN   
33        2708           4 2023-03-20 00:00:00.000               NaN   
34         454           1 2023-03-20 00:00:00.000               NaN   
35         454           2 2023-03-20 00:00:00.000               NaN   
36         454           3 2023-03-20 00:00:00.000               NaN   
37         454           4 2023-03-20 00:00:00.000               NaN   
38         224           1 2023-03-20 00:00:00.000               NaN   
39         224           2 2023-03-20 00:00:00.000               NaN   
40         224           3 2023-03-20 00:00:00.000               NaN   
41         224           4 2023-03-20 00:00:00.000               NaN   
42        1551           1 2023-03-20 00:00:00.000               NaN   
43        1551           2 2023-03-20 00:00:00.000               NaN   
44        1551           3 2023-03-20 00:00:00.000               NaN   
45        1551           4 2023-03-20 00:00:00.000               NaN   
46         225           1 2023-03-20 00:00:00.000               NaN   
47         225           2 2023-03-20 00:00:00.000               NaN   
48         225           3 2023-03-20 00:00:00.000               NaN   
49         225           4 2023-03-20 00:00:00.000               NaN   
50         235           1 2023-03-20 00:00:00.000               NaN   
51         235           2 2023-03-20 00:00:00.000               NaN   
52         235           3 2023-03-20 00:00:00.000               NaN   
53         235           4 2023-03-20 00:00:00.000               NaN   
54         611           1 2023-03-20 00:00:00.0

In [9]:
client = bigquery.Client(project = 'wf-gcp-us-ae-sf-prod')

# run update for update table
job_config = bigquery.LoadJobConfig(schema=[
    bigquery.SchemaField(name="PageID", field_type="INTEGER"),
    bigquery.SchemaField(name="PlatformID", field_type="INTEGER"),
    bigquery.SchemaField(name="StartDate", field_type="DATETIME"),
    bigquery.SchemaField(name="SpeedIndexBudget", field_type="INTEGER"),
    bigquery.SchemaField(name="SpeedIndexGoal", field_type="INTEGER"),
    bigquery.SchemaField(name="TotalPageLoadTimeBudget", field_type="INTEGER"),
    bigquery.SchemaField(name="TotalPageLoadTimeGoal", field_type="INTEGER"),
    bigquery.SchemaField(name="HTMLSizeBudget", field_type="INTEGER"),
    bigquery.SchemaField(name="HTMLSizeGoal", field_type="INTEGER"),
    bigquery.SchemaField(name="SpeedIndexBudget99th", field_type="INTEGER"),
    bigquery.SchemaField(name="SpeedIndexGoal99th", field_type="INTEGER"),
    bigquery.SchemaField(name="TotalPageLoadTimeBudget99th", field_type="INTEGER"),
    bigquery.SchemaField(name="TotalPageLoadTimeGoal99th", field_type="INTEGER"),
    bigquery.SchemaField(name="SpeedIndexBudget75th", field_type="INTEGER"),
    bigquery.SchemaField(name="SpeedIndexGoal75th", field_type="INTEGER"),
    bigquery.SchemaField(name="SpeedIndexBudget95th", field_type="INTEGER"),
    bigquery.SchemaField(name="SpeedIndexGoal95th", field_type="INTEGER"),
    bigquery.SchemaField(name="ingest_timestamp", field_type="TIMESTAMP"),
    bigquery.SchemaField(name="event_date", field_type="DATE")], write_disposition="WRITE_APPEND")
update_t = client.load_table_from_dataframe(update_slo_table,
                                            'wf-gcp-us-ae-sf-prod.junk.si_slo_update_test',
                                            job_config=job_config)
update_t.result()

LoadJob<project=wf-gcp-us-ae-sf-prod, location=US, id=1072a5a0-bf2d-4cf9-ac88-39345289dd7e>